# Build Fingerprint Recognition Model

In [5]:
# Creating a visual demo notebook version of the fingerprint recognition model training and inference

# 🧠 Fingerprint Recognition with Metric Learning (SOCOFing Dataset)

'''This notebook demonstrates how to build a scalable fingerprint recognition system using PyTorch and the SOCOFing dataset.
We'll leverage metric learning to train a model that can effectively compare fingerprints and identify matches.'''

## 📦 Step 1: Setup & Imports

import os
import torch
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader
from torchvision import transforms, models
from PIL import Image
import random
from sklearn.metrics.pairwise import cosine_similarity
import numpy as np


In [1]:
import torch
print(torch.cuda.is_available())       # Should return True
print(torch.cuda.get_device_name(0))   # GPU name


True
NVIDIA GeForce RTX 4050 Laptop GPU


In [ ]:
import kagglehub

# Download latest version
path = kagglehub.dataset_download("ruizgara/socofing")
path = path + "/SOCOFing/Real/"
print("Path to dataset files:", path)

Path to dataset files: /kaggle/input/socofing/SOCOFing/Real/


In [2]:
path="C:\\Users\\srish\\Downloads\\archive\\SOCOFing\\Real"

In [6]:
class SOCOFingDataset(Dataset):
    def __init__(self, image_folder, transform=None):
        self.image_folder = image_folder
        self.transform = transform
        # Modified to ensure only valid image paths are considered
        self.image_paths = [
            os.path.join(image_folder, fname)
            for fname in os.listdir(image_folder)
            if fname.endswith('.BMP') and os.path.isfile(os.path.join(image_folder, fname))
        ]
        # Check if image_paths is empty and handle it
        if not self.image_paths:
            raise ValueError(f"No .BMP image files found in the directory: {image_folder}")

        self.label_map = self._build_label_map()

    def _build_label_map(self):
        labels = set()
        for path in self.image_paths:
            person_id = int(os.path.basename(path).split('__')[0])
            labels.add(person_id)
        return {label: idx for idx, label in enumerate(sorted(labels))}

    def __len__(self):
        return len(self.image_paths)

    def __getitem__(self, idx):
        anchor_path = self.image_paths[idx]
        anchor_label = int(os.path.basename(anchor_path).split('__')[0])
        anchor_image = Image.open(anchor_path).convert('L')

        positive_path = random.choice([p for p in self.image_paths if f"{anchor_label}__" in p and p != anchor_path])
        negative_path = random.choice([p for p in self.image_paths if f"{anchor_label}__" not in p])

        positive_image = Image.open(positive_path).convert('L')
        negative_image = Image.open(negative_path).convert('L')

        if self.transform:
            anchor_image = self.transform(anchor_image)
            positive_image = self.transform(positive_image)
            negative_image = self.transform(negative_image)

        return anchor_image, positive_image, negative_image

In [7]:
#CNN EMBEDDING MODEL (ResNet18)

class FingerprintNet(nn.Module):
    def __init__(self, embedding_dim=128):
        super().__init__()
        self.backbone = models.resnet18(pretrained=True)
        self.backbone.conv1 = nn.Conv2d(1, 64, kernel_size=7, stride=2, padding=3, bias=False)
        self.backbone.fc = nn.Linear(self.backbone.fc.in_features, embedding_dim)

    def forward(self, x):
        return self.backbone(x)


In [8]:
class TripletLoss(nn.Module):
    def __init__(self, margin=1.0):
        super().__init__()
        self.loss_fn = nn.TripletMarginLoss(margin=margin)

    def forward(self, anchor, positive, negative):
        return self.loss_fn(anchor, positive, negative)


In [9]:
def train_model(data_dir, model_save_path="fingerprint_model.pth", epochs=10):
    transform = transforms.Compose([
        transforms.Resize((224, 224)),
        transforms.ToTensor()
    ])
    dataset = SOCOFingDataset(data_dir, transform=transform)
    dataloader = DataLoader(dataset, batch_size=32, shuffle=True)

    model = FingerprintNet().cuda()
    optimizer = torch.optim.Adam(model.parameters(), lr=1e-4)
    criterion = TripletLoss()

    for epoch in range(epochs):
        model.train()
        total_loss = 0
        for anchor, positive, negative in dataloader:
            anchor, positive, negative = anchor.cuda(), positive.cuda(), negative.cuda()
            anchor_out = model(anchor)
            positive_out = model(positive)
            negative_out = model(negative)

            loss = criterion(anchor_out, positive_out, negative_out)
            optimizer.zero_grad()
            loss.backward()
            optimizer.step()
            total_loss += loss.item()
        print(f"Epoch {epoch+1}, Loss: {total_loss:.4f}")

    torch.save(model.state_dict(), model_save_path)
    return model, transform


In [10]:
def build_embedding_db(model, image_folder, transform):
    model.eval()
    embeddings, labels = [], []
    paths = [os.path.join(image_folder, fname) for fname in os.listdir(image_folder) if fname.endswith('.BMP')]

    with torch.no_grad():
        for path in paths:
            img = Image.open(path).convert('L')
            img_tensor = transform(img).unsqueeze(0).cuda()
            embedding = model(img_tensor).cpu().numpy().flatten()
            embeddings.append(embedding)
            labels.append(path)

    return embeddings, labels


In [11]:
def predict_identity(model, query_image_path, db_embeddings, db_labels, transform):
    model.eval()
    img = Image.open(query_image_path).convert('L')
    img_tensor = transform(img).unsqueeze(0).cuda()

    with torch.no_grad():
        query_embedding = model(img_tensor).cpu().numpy().flatten()

    sims = cosine_similarity([query_embedding], db_embeddings)[0]
    best_match_idx = np.argmax(sims)
    return db_labels[best_match_idx], sims[best_match_idx]


In [12]:
# Train the model
model, transform = train_model(path, epochs=15)

# Build DB
db_embeddings, db_labels = build_embedding_db(model, path, transform)



d:\Biometric attendance\.venv\Lib\site-packages\torchvision\models\_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
d:\Biometric attendance\.venv\Lib\site-packages\torchvision\models\_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=ResNet18_Weights.IMAGENET1K_V1`. You can also use `weights=ResNet18_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)


Epoch 1, Loss: 124.1026
Epoch 2, Loss: 104.6950
Epoch 3, Loss: 91.4984
Epoch 4, Loss: 84.4969
Epoch 5, Loss: 84.7596
Epoch 6, Loss: 73.2770
Epoch 7, Loss: 68.7182
Epoch 8, Loss: 66.4407
Epoch 9, Loss: 59.0720
Epoch 10, Loss: 55.3691
Epoch 11, Loss: 55.4512
Epoch 12, Loss: 53.1652
Epoch 13, Loss: 51.4517
Epoch 14, Loss: 47.5000
Epoch 15, Loss: 53.2575


In [14]:
# Predict an identity
query_path = path+"\\51__M_Right_index_finger.BMP"
matched_file, confidence = predict_identity(model, query_path, db_embeddings, db_labels, transform)
print(f"Matched file: {matched_file} \nSimilarity score: {confidence:.4f}")


Matched file: C:\Users\srish\Downloads\archive\SOCOFing\Real\51__M_Right_index_finger.BMP 
Similarity score: 1.0000


In [ ]:
query_path = "/kaggle/input/socofing/SOCOFing/Altered/Altered-Easy/100__M_Left_index_finger_Obl.BMP"
matched_file, confidence = predict_identity(model, query_path, db_embeddings, db_labels, transform)
print(f"Matched file: {matched_file} \nSimilarity score: {confidence:.4f}")


Matched file: /kaggle/input/socofing/SOCOFing/Real/100__M_Left_index_finger.BMP 
Similarity score: 0.9937


In [ ]:
query_path = "/kaggle/input/socofing/SOCOFing/Altered/Altered-Hard/100__M_Right_little_finger_CR.BMP"
matched_file, confidence = predict_identity(model, query_path, db_embeddings, db_labels, transform)
print(f"Matched file: {matched_file} \nSimilarity score: {confidence:.4f}")


Matched file: /kaggle/input/socofing/SOCOFing/Real/544__M_Right_middle_finger.BMP 
Similarity score: 0.9861


In [ ]:
query_path = "/kaggle/input/socofing/SOCOFing/Altered/Altered-Easy/100__M_Left_index_finger_Obl.BMP"
matched_file, confidence = predict_identity(model, query_path, db_embeddings, db_labels, transform)
print(f"Matched file: {matched_file} \nSimilarity score: {confidence:.4f}")


Matched file: /kaggle/input/socofing/SOCOFing/Real/100__M_Left_index_finger.BMP 
Similarity score: 0.9937


In [ ]:
query_path = "/kaggle/input/socofing/SOCOFing/Altered/Altered-Medium/100__M_Right_thumb_finger_CR.BMP"
matched_file, confidence = predict_identity(model, query_path, db_embeddings, db_labels, transform)
print(f"Matched file: {matched_file} \nSimilarity score: {confidence:.4f}")


Matched file: /kaggle/input/socofing/SOCOFing/Real/100__M_Right_thumb_finger.BMP 
Similarity score: 0.9916


In [ ]:
query_path = "/kaggle/input/socofing/SOCOFing/Altered/Altered-Easy/100__M_Left_index_finger_Obl.BMP"
matched_file, confidence = predict_identity(model, query_path, db_embeddings, db_labels, transform)
print(f"Matched file: {matched_file} \nSimilarity score: {confidence:.4f}")


Matched file: /kaggle/input/socofing/SOCOFing/Real/100__M_Left_index_finger.BMP 
Similarity score: 0.9937


In [ ]:
while True:
    query_path = input("Enter the fingerprint image path (or type 'exit' to quit): ").strip()

    if query_path.lower() == 'exit':
        print("Exiting...")
        break

    try:
        matched_file, confidence = predict_identity(model, query_path, db_embeddings, db_labels, transform)
        print(f"Matched file: {matched_file} \nSimilarity score: {confidence:.4f}")
    except Exception as e:
        print(f"Error: {e}")


Enter the fingerprint image path (or type 'exit' to quit): /kaggle/input/socofing/SOCOFing/Altered/Altered-Medium/100__M_Right_middle_finger_Zcut.BMP
Matched file: /kaggle/input/socofing/SOCOFing/Real/100__M_Right_middle_finger.BMP 
Similarity score: 0.9927
Enter the fingerprint image path (or type 'exit' to quit): /kaggle/input/socofing/SOCOFing/Altered/Altered-Medium/101__M_Right_ring_finger_Obl.BMP
Matched file: /kaggle/input/socofing/SOCOFing/Real/418__F_Right_little_finger.BMP 
Similarity score: 0.9862
Enter the fingerprint image path (or type 'exit' to quit): exit
Exiting...


In [15]:
import os
from glob import glob

# Prompt user for a directory containing BMP files
#folder_path = input("Enter the path to the folder containing .BMP files (or type 'exit' to quit): ").strip()
folder_path= path

if folder_path.lower() == 'exit':
    print("Exiting...")
else:
    if not os.path.isdir(folder_path):
        print("Invalid folder path.")
    else:
        bmp_files = glob(os.path.join(folder_path, '*.BMP'))

        if not bmp_files:
            print("No .BMP files found in the folder.")
        else:
            for query_path in bmp_files:
                try:
                    matched_file, confidence = predict_identity(model, query_path, db_embeddings, db_labels, transform)
                    print(f"File: {os.path.basename(query_path)}")
                    print(f" → Matched file: {matched_file}")
                    print(f" → Similarity score: {confidence:.4f}\n")
                except Exception as e:
                    print(f"Error processing {query_path}: {e}")


File: 100__M_Left_index_finger.BMP
 → Matched file: C:\Users\srish\Downloads\archive\SOCOFing\Real\100__M_Left_index_finger.BMP
 → Similarity score: 1.0000

File: 100__M_Left_little_finger.BMP
 → Matched file: C:\Users\srish\Downloads\archive\SOCOFing\Real\100__M_Left_little_finger.BMP
 → Similarity score: 1.0000

File: 100__M_Left_middle_finger.BMP
 → Matched file: C:\Users\srish\Downloads\archive\SOCOFing\Real\100__M_Left_middle_finger.BMP
 → Similarity score: 1.0000

File: 100__M_Left_ring_finger.BMP
 → Matched file: C:\Users\srish\Downloads\archive\SOCOFing\Real\100__M_Left_ring_finger.BMP
 → Similarity score: 1.0000

File: 100__M_Left_thumb_finger.BMP
 → Matched file: C:\Users\srish\Downloads\archive\SOCOFing\Real\100__M_Left_thumb_finger.BMP
 → Similarity score: 1.0000

File: 100__M_Right_index_finger.BMP
 → Matched file: C:\Users\srish\Downloads\archive\SOCOFing\Real\100__M_Right_index_finger.BMP
 → Similarity score: 1.0000

File: 100__M_Right_little_finger.BMP
 → Matched file: 

In [ ]:
!pip install matplotlib pillow


In [ ]:
import os
from glob import glob

def extract_identity(filename):
    """Extract the identity from the filename (before the first '__')."""
    return filename.split('__')[0]

# Initialize counters
correct = 0
incorrect = 0
total = 0

# Get folder input
folder_path = input("Enter the path to the folder containing .BMP files (or type 'exit' to quit): ").strip()

if folder_path.lower() == 'exit':
    print("Exiting...")
else:
    if not os.path.isdir(folder_path):
        print("Invalid folder path.")
    else:
        bmp_files = glob(os.path.join(folder_path, '*.BMP'))

        if not bmp_files:
            print("No .BMP files found in the folder.")
        else:
            for query_path in bmp_files:
                try:
                    matched_file, confidence = predict_identity(model, query_path, db_embeddings, db_labels, transform)

                    query_id = extract_identity(os.path.basename(query_path))
                    matched_id = extract_identity(os.path.basename(matched_file))

                    print(f"\nQuery: {os.path.basename(query_path)}")
                    print(f"Matched: {os.path.basename(matched_file)}")
                    print(f"Similarity: {confidence:.4f}")

                    total += 1
                    if query_id == matched_id:
                        correct += 1
                    else:
                        incorrect += 1

                except Exception as e:
                    print(f"Error processing {query_path}: {e}")

# Final report
print("\n=== Match Summary ===")
print(f"Total files processed: {total}")
print(f"Correct matches: {correct}")
print(f"Incorrect matches: {incorrect}")
accuracy = (correct / total) * 100 if total > 0 else 0
print(f"Accuracy: {accuracy:.2f}%")


Streaming output truncated to the last 5000 lines.
Matched: 496__M_Left_thumb_finger.BMP
Similarity: 0.9890

Query: 68__M_Left_middle_finger_CR.BMP
Matched: 96__M_Left_ring_finger.BMP
Similarity: 0.9934

Query: 20__M_Left_thumb_finger_Obl.BMP
Matched: 209__F_Left_middle_finger.BMP
Similarity: 0.9830

Query: 356__M_Left_index_finger_CR.BMP
Matched: 356__M_Left_index_finger.BMP
Similarity: 0.9931

Query: 121__F_Left_middle_finger_Obl.BMP
Matched: 342__M_Left_index_finger.BMP
Similarity: 0.9878

Query: 543__M_Right_ring_finger_Obl.BMP
Matched: 529__M_Right_little_finger.BMP
Similarity: 0.9923

Query: 243__M_Right_ring_finger_Zcut.BMP
Matched: 243__M_Right_ring_finger.BMP
Similarity: 0.9977

Query: 10__M_Left_thumb_finger_CR.BMP
Matched: 419__F_Right_thumb_finger.BMP
Similarity: 0.9923

Query: 290__M_Left_middle_finger_CR.BMP
Matched: 357__M_Right_middle_finger.BMP
Similarity: 0.9890

Query: 362__M_Right_thumb_finger_Zcut.BMP
Matched: 20__M_Left_ring_finger.BMP
Similarity: 0.9891

Query: 4

In [ ]:
#medium altered
import os
from glob import glob

def extract_identity(filename):
    """Extract the identity from the filename (before the first '__')."""
    return filename.split('__')[0]

# Initialize counters
correct = 0
incorrect = 0
total = 0

# Get folder input
folder_path = input("Enter the path to the folder containing .BMP files (or type 'exit' to quit): ").strip()

if folder_path.lower() == 'exit':
    print("Exiting...")
else:
    if not os.path.isdir(folder_path):
        print("Invalid folder path.")
    else:
        bmp_files = glob(os.path.join(folder_path, '*.BMP'))

        if not bmp_files:
            print("No .BMP files found in the folder.")
        else:
            for query_path in bmp_files:
                try:
                    matched_file, confidence = predict_identity(model, query_path, db_embeddings, db_labels, transform)

                    query_id = extract_identity(os.path.basename(query_path))
                    matched_id = extract_identity(os.path.basename(matched_file))

                    print(f"\nQuery: {os.path.basename(query_path)}")
                    print(f"Matched: {os.path.basename(matched_file)}")
                    print(f"Similarity: {confidence:.4f}")

                    total += 1
                    if query_id == matched_id:
                        correct += 1
                    else:
                        incorrect += 1

                except Exception as e:
                    print(f"Error processing {query_path}: {e}")

# Final report
print("\n=== Match Summary ===")
print(f"Total files processed: {total}")
print(f"Correct matches: {correct}")
print(f"Incorrect matches: {incorrect}")
accuracy = (correct / total) * 100 if total > 0 else 0
print(f"Accuracy: {accuracy:.2f}%")


Streaming output truncated to the last 5000 lines.
Matched: 129__M_Right_little_finger.BMP
Similarity: 0.9957

Query: 600__M_Right_middle_finger_Zcut.BMP
Matched: 564__M_Left_ring_finger.BMP
Similarity: 0.9893

Query: 594__M_Right_index_finger_Zcut.BMP
Matched: 594__M_Right_index_finger.BMP
Similarity: 0.9951

Query: 498__M_Right_ring_finger_CR.BMP
Matched: 242__M_Right_index_finger.BMP
Similarity: 0.9934

Query: 444__M_Left_ring_finger_CR.BMP
Matched: 332__M_Left_thumb_finger.BMP
Similarity: 0.9898

Query: 412__M_Right_index_finger_Obl.BMP
Matched: 91__F_Left_middle_finger.BMP
Similarity: 0.9918

Query: 290__M_Right_middle_finger_Obl.BMP
Matched: 367__M_Right_middle_finger.BMP
Similarity: 0.9887

Query: 597__M_Right_middle_finger_Zcut.BMP
Matched: 597__M_Right_middle_finger.BMP
Similarity: 0.9920

Query: 299__M_Left_thumb_finger_CR.BMP
Matched: 299__M_Left_thumb_finger.BMP
Similarity: 0.9917

Query: 458__M_Right_index_finger_Obl.BMP
Matched: 458__M_Right_index_finger.BMP
Similarity: 0

In [17]:
#Easy altered
import os
from glob import glob

def extract_identity(filename):
    """Extract the identity from the filename (before the first '__')."""
    return filename.split('__')[0]

# Initialize counters
correct = 0
incorrect = 0
total = 0

# Get folder input
#folder_path = input("Enter the path to the folder containing .BMP files (or type 'exit' to quit): ").strip()
folder_path = "C:\\Users\\srish\\Downloads\\archive\\SOCOFing\\Altered\\Altered-Easy"
if folder_path.lower() == 'exit':
    print("Exiting...")
else:
    if not os.path.isdir(folder_path):
        print("Invalid folder path.")
    else:
        bmp_files = glob(os.path.join(folder_path, '*.BMP'))

        if not bmp_files:
            print("No .BMP files found in the folder.")
        else:
            for query_path in bmp_files:
                try:
                    matched_file, confidence = predict_identity(model, query_path, db_embeddings, db_labels, transform)

                    query_id = extract_identity(os.path.basename(query_path))
                    matched_id = extract_identity(os.path.basename(matched_file))

                    print(f"\nQuery: {os.path.basename(query_path)}")
                    print(f"Matched: {os.path.basename(matched_file)}")
                    print(f"Similarity: {confidence:.4f}")

                    total += 1
                    if query_id == matched_id:
                        correct += 1
                    else:
                        incorrect += 1

                except Exception as e:
                    print(f"Error processing {query_path}: {e}")

# Final report
print("\n=== Match Summary ===")
print(f"Total files processed: {total}")
print(f"Correct matches: {correct}")
print(f"Incorrect matches: {incorrect}")
accuracy = (correct / total) * 100 if total > 0 else 0
print(f"Accuracy: {accuracy:.2f}%")



Query: 13__F_Left_ring_finger_Zcut.BMP
Matched: 13__F_Left_ring_finger.BMP
Similarity: 0.9972

Query: 13__F_Left_thumb_finger_CR.BMP
Matched: 13__F_Left_thumb_finger.BMP
Similarity: 0.9920

Query: 13__F_Left_thumb_finger_Obl.BMP
Matched: 13__F_Left_thumb_finger.BMP
Similarity: 0.9819

Query: 13__F_Left_thumb_finger_Zcut.BMP
Matched: 13__F_Left_thumb_finger.BMP
Similarity: 0.9968

Query: 13__F_Right_index_finger_CR.BMP
Matched: 13__F_Right_index_finger.BMP
Similarity: 0.9914

Query: 13__F_Right_index_finger_Obl.BMP
Matched: 13__F_Right_index_finger.BMP
Similarity: 0.9874

Query: 13__F_Right_index_finger_Zcut.BMP
Matched: 13__F_Right_index_finger.BMP
Similarity: 0.9994

Query: 13__F_Right_little_finger_CR.BMP
Matched: 13__F_Right_little_finger.BMP
Similarity: 0.9965

Query: 13__F_Right_little_finger_Obl.BMP
Matched: 13__F_Right_little_finger.BMP
Similarity: 0.9721

Query: 13__F_Right_little_finger_Zcut.BMP
Matched: 13__F_Right_little_finger.BMP
Similarity: 0.9984

Query: 13__F_Right_mid